## County Example from https://plot.ly/python/choropleth-maps/
More <a href="https://plot.ly/python/county-choropleth/">county examples</a>  - note first Figure Factory examples are now deprecated
<p>Need to install plotly-geo and geopandas

<p>conda install -c plotly plotly-geo
<p>conda install -c conda-forge geopandas

In [ ]:
#Deprecated choropleth using figure factory
import chart_studio.plotly as py
import plotly.figure_factory as ff
from plotly.offline import iplot, init_notebook_mode
init_notebook_mode(connected=True)

import numpy as np
import pandas as pd

df_sample = pd.read_csv('https://raw.githubusercontent.com/plotly/datasets/master/laucnty16.csv')
df_sample['State FIPS Code'] = df_sample['State FIPS Code'].apply(lambda x: str(x).zfill(2))
df_sample['County FIPS Code'] = df_sample['County FIPS Code'].apply(lambda x: str(x).zfill(3))
df_sample['FIPS'] = df_sample['State FIPS Code'] + df_sample['County FIPS Code']

colorscale = ["#f7fbff", "#ebf3fb", "#deebf7", "#d2e3f3", "#c6dbef", "#b3d2e9", "#9ecae1",
    "#85bcdb", "#6baed6", "#57a0ce", "#4292c6", "#3082be", "#2171b5", "#1361a9",
    "#08519c", "#0b4083", "#08306b"
]
endpts = list(np.linspace(1, 12, len(colorscale) - 1))
fips = df_sample['FIPS'].tolist()
values = df_sample['Unemployment Rate (%)'].tolist()

fig = ff.create_choropleth(
    fips = fips, values = values, scope = ['usa'],
    binning_endpoints = endpts, colorscale = colorscale,
    show_state_data = False,
    show_hover = True, centroid_marker = {
        'opacity': 0
    },
    asp = 2.9,
    title = 'USA by Unemployment %',
    legend_title = '% unemployed'
)
iplot(fig, filename = 'choropleth_full_usa') 
#      include_plotlyjs='https://cdn.plot.ly/plotly-1.42.3.min.js')

## Plotly example of using county poverty data  
See previous poverty notebook for folium example for comparison.
Note no geojson files need to be read. 
<p> County choropleths can be created with ff.create_choropleth() but hover does not work in offline mode with iplot. It does work in offline mode with plot - see <a href="https://katie.mtech.edu/classes/csci444/choropleth_full_usa.html">map</a> and code on katie. (An older version of plotly js is required for the hover to work.)

In [ ]:
#deprecated version using Figure Factory
import chart_studio.plotly as py
import plotly.figure_factory as ff
from plotly.offline import iplot, init_notebook_mode
init_notebook_mode(connected=True)

import numpy as np
import pandas as pd

df = pd.read_excel("https://katie.mtech.edu/classes/csci444/notebooks/data/PovertyEstimatesCounties.xls", 
                   sheet_name="Poverty Data 2016", skiprows=range(3))

#Filter out rows with state totals
df = df[df['FIPStxt']%1000 != 0]

             
colorscale = ['rgb(255,255,204)', 'rgb(255,237,160)', 'rgb(254,217,118)', 'rgb(254,178,76)', 'rgb(253,141,60)', 
              'rgb(252,78,42)', 'rgb(227,26,28)', 'rgb(189,0,38)', 'rgb(128,0,38)']


endpts = list(np.linspace(1, 50, len(colorscale) - 1))

fips = df['FIPStxt'].tolist()
values = df['PCTPOVALL_2016'].tolist()

fig = ff.create_choropleth(
    fips = fips, values = values, scope = ['usa'],
    binning_endpoints = endpts, 
    colorscale = colorscale,
    show_state_data = False,
    county_outline={'color': 'rgb(15, 15, 55)', 'width': 0.2},
    show_hover = True, centroid_marker = {
        'opacity': 0
    },
    asp = 2.9,
    title = 'USA Poverty %',
    legend_title = '% poverty'
)
iplot(fig, filename = 'choropleth_poverty_usa')

##  Can use plotly go.Choropleth() for US states and countries
Hover works here and map is interactive, but there is no location mode for counties

In [ ]:
import chart_studio.plotly as py
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
init_notebook_mode(connected=True)

import numpy as np
import pandas as pd

df = pd.read_excel("https://katie.mtech.edu/classes/csci444/notebooks/data/PovertyEstimatesCounties.xls", 
                   sheet_name="Poverty Data 2016", skiprows=range(3))

#Select rows with state totals
df = df[df['FIPStxt']%1000 == 0]

#Text for hover data
df['text'] = df['Area_Name'] #+ '<br>' + df['PCTPOVALL_2016'].astype(str)
             
data = [go.Choropleth(
    colorscale = 'YlOrRd',
    autocolorscale = False,
    reversescale = True,
    locations = df['State'],
    z = df['PCTPOVALL_2016'].astype(float),
    locationmode = 'USA-states',
    text = df['text'],
    marker = go.choropleth.Marker(
        line = go.choropleth.marker.Line(
            color = 'rgb(255,255,255)',
            width = 2
        )),
    colorbar = go.choropleth.ColorBar(
        title = "%Poverty")
)]

layout = go.Layout(
    title = go.layout.Title(
        text = 'State Poverty %'
    ),
    geo = go.layout.Geo(
        scope = 'usa',
        projection = go.layout.geo.Projection(type = 'albers usa'),
        showlakes = True,
        lakecolor = 'rgb(255, 255, 255)'),
)

fig = go.Figure(data = data, layout = layout)
iplot(fig, filename = 'poverty-cloropleth-map')


In [ ]:
#preferred method using Plotly Express with a GeoJSON

from urllib.request import urlopen
import json
with urlopen('https://raw.githubusercontent.com/plotly/datasets/master/geojson-counties-fips.json') as response:
    counties = json.load(response)

import pandas as pd
df = pd.read_csv("https://raw.githubusercontent.com/plotly/datasets/master/fips-unemp-16.csv",
                   dtype={"fips": str})

import plotly.express as px

fig = px.choropleth(df, geojson=counties, locations='fips', color='unemp',
                           color_continuous_scale="Viridis",
                           range_color=(0, 12),
                           scope="usa",
                           labels={'unemp':'unemployment rate'}
                          )
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [ ]:
#Using our Poverty Estimate spreadsheet with Plotly Express
import numpy as np
import pandas as pd

df = pd.read_excel("https://katie.mtech.edu/classes/csci444/notebooks/data/PovertyEstimatesCounties.xls", 
                   sheet_name="Poverty Data 2016", skiprows=range(3),dtype={"FIPStxt": str})
   
from urllib.request import urlopen
import json
with urlopen('https://raw.githubusercontent.com/plotly/datasets/master/geojson-counties-fips.json') as response:
    counties = json.load(response)

import plotly.express as px

fig = px.choropleth(df, geojson=counties, locations='FIPStxt', color='PCTPOVALL_2016',
                           color_continuous_scale="YlOrRd",
                           range_color=(0, 50),
                           scope="usa",
                           labels={'PCTPOVALL_2016':'Percent'}
                          )
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

## Plotly mapbox 

https://plot.ly/python/mapbox-county-choropleth/

In [ ]:
#Using Plotly mapbox with poverty data 
from urllib.request import urlopen
import json
with urlopen('https://raw.githubusercontent.com/plotly/datasets/master/geojson-counties-fips.json') as response:
    counties = json.load(response)

import pandas as pd
df = pd.read_excel("https://katie.mtech.edu/classes/csci444/notebooks/data/PovertyEstimatesCounties.xls", 
                   sheet_name="Poverty Data 2016", skiprows=range(3),dtype={"FIPStxt": str})

import plotly.graph_objects as go

fig = go.Figure(go.Choroplethmapbox(geojson=counties, locations=df.FIPStxt, z=df.PCTPOVALL_2016,
                                    colorscale="YlOrRd", zmin=0, zmax=50,
                                    marker_opacity=0.5, marker_line_width=0))
fig.update_layout(mapbox_style="carto-positron",
                  mapbox_zoom=3, mapbox_center = {"lat": 37.0902, "lon": -95.7129})
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

## Choropleth map using scattermapbox
Other techniques exist to create a choropleth map. Here are links to one Dash example:
<p> <a href="https://github.com/plotly/dash-opioid-epidemic-demo/blob/master/app.py">Code</a>
<p> <a href="https://opioid-epidemic.herokuapp.com/">App</a>